In [11]:
import importlib

# Imports
from rdkit import Chem
from rdkit.Chem import AllChem
import pandas as pd
from scipy.stats import zscore
import matplotlib.pyplot as plt 
import defaults
importlib.reload(defaults)

<module 'defaults' from 'C:\\Users\\20223037\\OneDrive - TU Eindhoven\\Documents\\school\\jaar2\\Biomedical\\8CC00-GroupAssignment\\defaults.py'>

In [12]:
# Read data and construct dataframe

df = pd.read_csv('datasets/tested_molecules.csv')

df.head()

SMILES  PKM2_inhibition  ERK2_inhibition
0                 C=C(C)c1nc(N)nc(N)n1                0                0
1       C=C(Cl)COc1ccc2c(C)cc(=O)oc2c1                0                0
2              C=CCNC(=O)CCCC(=O)NCC=C                0                0
3  C=CCOn1c(=O)c(C)[n+]([O-])c2ccccc21                0                0
4         C=CCn1cc(Cl)c(=O)n(CC=C)c1=O                0                0

In [13]:
# Load the dataset
df = pd.read_csv('datasets/tested_molecules.csv')  # Replace with your file path

# Function to compute descriptors
def compute_descriptors(smiles):
    mol = Chem.MolFromSmiles(smiles)
    if mol:
        return defaults.get_mol_descriptors(mol)
    else:
        return {key: None for key in defaults.x_data}

df['Descriptors'] = df['SMILES'].apply(compute_descriptors)
descriptors_df = pd.json_normalize(df['Descriptors'])
df = pd.concat([df, descriptors_df], axis=1).drop(columns=['Descriptors'])
df.head()

SMILES  PKM2_inhibition  ERK2_inhibition  \
0                 C=C(C)c1nc(N)nc(N)n1                0                0   
1       C=C(Cl)COc1ccc2c(C)cc(=O)oc2c1                0                0   
2              C=CCNC(=O)CCCC(=O)NCC=C                0                0   
3  C=CCOn1c(=O)c(C)[n+]([O-])c2ccccc21                0                0   
4         C=CCn1cc(Cl)c(=O)n(CC=C)c1=O                0                0   

   EState_VSA7  SMR_VSA10  fr_thiazole  PEOE_VSA3     Chi1v    MolWt  \
0     0.000000  17.469783            0   0.000000  3.022544  151.173   
1    12.990104  22.570184            0   4.794537  5.444609  250.681   
2     0.000000  11.814359            0   0.000000  4.955455  210.277   
3     0.000000  11.033401            0   0.000000  5.146222  232.239   
4     0.000000  11.600940            0   4.794537  4.708338  226.663   

       Chi1  ...  PEOE_VSA1  HeavyAtomMolWt  SMR_VSA9  VSA_EState6    AvgIpc  \
0  5.092224  ...  11.467335         142.101  0.000000     0.000000  1.846047   
1  8.058551  ...   9.154014         239.593  5.749512     6.779888  2.250829   
2  7.201907  ...  10.633577         192.133  0.000000     0.000000  2.231161   
3  8.163902  ...  10.044842         220.143  0.000000     6.777354  2.361815   
4  7.112591  ...   0.000000         215.575  0.000000     0.000000  2.211254   

   FractionCSP3     Chi3v   LabuteASA  BCUT2D_MRLOW  RingCount  
0      0.166667  1.051723   64.175352      1.044248          1  
1      0.153846  2.427385  103.266383      0.359025          2  
2      0.454545  1.694814   90.432235     -0.121740          0  
3      0.166667  2.439419   97.719850     -0.585723          2  
4      0.200000  2.091973   91.727399      0.625699          1  

[5 rows x 59 columns]

In [14]:
# Convert SMILES to fingerprints, so we have usable data training

def smiles_to_fingerprint(smiles):
    mol = Chem.MolFromSmiles(smiles)
    if mol:
        fp = AllChem.GetMorganFingerprintAsBitVect(mol, 2, nBits=1024)
        return list(fp)
    else:
        return [0] * 1024
    
df['Fingerprint'] = df['SMILES'].apply(smiles_to_fingerprint)

df.head()

SMILES  PKM2_inhibition  ERK2_inhibition  \
0                 C=C(C)c1nc(N)nc(N)n1                0                0   
1       C=C(Cl)COc1ccc2c(C)cc(=O)oc2c1                0                0   
2              C=CCNC(=O)CCCC(=O)NCC=C                0                0   
3  C=CCOn1c(=O)c(C)[n+]([O-])c2ccccc21                0                0   
4         C=CCn1cc(Cl)c(=O)n(CC=C)c1=O                0                0   

   EState_VSA7  SMR_VSA10  fr_thiazole  PEOE_VSA3     Chi1v    MolWt  \
0     0.000000  17.469783            0   0.000000  3.022544  151.173   
1    12.990104  22.570184            0   4.794537  5.444609  250.681   
2     0.000000  11.814359            0   0.000000  4.955455  210.277   
3     0.000000  11.033401            0   0.000000  5.146222  232.239   
4     0.000000  11.600940            0   4.794537  4.708338  226.663   

       Chi1  ...  HeavyAtomMolWt  SMR_VSA9  VSA_EState6    AvgIpc  \
0  5.092224  ...         142.101  0.000000     0.000000  1.846047   
1  8.058551  ...         239.593  5.749512     6.779888  2.250829   
2  7.201907  ...         192.133  0.000000     0.000000  2.231161   
3  8.163902  ...         220.143  0.000000     6.777354  2.361815   
4  7.112591  ...         215.575  0.000000     0.000000  2.211254   

   FractionCSP3     Chi3v   LabuteASA  BCUT2D_MRLOW  RingCount  \
0      0.166667  1.051723   64.175352      1.044248          1   
1      0.153846  2.427385  103.266383      0.359025          2   
2      0.454545  1.694814   90.432235     -0.121740          0   
3      0.166667  2.439419   97.719850     -0.585723          2   
4      0.200000  2.091973   91.727399      0.625699          1   

                                         Fingerprint  
0  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
1  [0, 0, 0, 1, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, ...  
2  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
3  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  
4  [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, ...  

[5 rows x 60 columns]

In [15]:
column_names = defaults.x_data
z_scores = df[defaults.x_data].apply(zscore)
rows_names = defaults.y_data

threshold = 2
lower_threshold = -2

# Create subplots for each variable
fig, axs = plt.subplots(len(column_names), len(rows_names), figsize=(20, len(column_names)*6))

for i, inhibition_enzyme in enumerate(defaults.y_data):
    # Iterate over each variable name
    for j, column_name in enumerate(column_names):
        # Compute z-scores for the specified column
        #z_scores = df[column_name].apply(zscore)
        
        # Extract the column values for PKM2_inhibition
        PKM2_inhibition = df[inhibition_enzyme]
        
        # Identify outliers based on z-scores exceeding the thresholds
        outliers = (z_scores.abs() > threshold).any(axis=1)
        
        # Extract z-scores for the column of interest
        z_scores_column = z_scores[column_name]
        
        # Define colors for the bars based on the ratio
        colors = PKM2_inhibition.map({0: 'skyblue', 1: 'orange'})
        
        # Plotting the histogram as a stacked bar histogram
        axs[j][i].hist(z_scores_column[PKM2_inhibition == 0], bins=80, color='skyblue', edgecolor='black', alpha=0.7, label=f'{column_name} = 0', stacked=True)
        axs[j][i].hist(z_scores_column[PKM2_inhibition == 1], bins=80, color='orange', edgecolor='black', alpha=0.7, label=f'{column_name} = 1', stacked=True)
        
        # Enhancing plot aesthetics and providing descriptive labels
        axs[j][i].set_title(f'Stacked Distribution of Standardized {column_name} Values based on {inhibition_enzyme}')
        axs[j][i].set_xlabel('Standardized LogP')
        axs[j][i].set_ylabel('Frequency')
        
        # Add vertical lines at the thresholds for visual reference
        axs[j][i].axvline(x=threshold, color='red', linestyle='--', label=f'Threshold ({threshold})')
        axs[j][i].axvline(x=lower_threshold, color='green', linestyle='--', label=f'Lower Threshold ({lower_threshold})')
        
        # Indicate the presence of the thresholds
        axs[j][i].text(threshold + 0.1, axs[j][i].get_ylim()[1] * 0.9, 'Upper Threshold', color='red')
        axs[j][i].text(lower_threshold - 0.5, axs[j][i].get_ylim()[1] * 0.9, 'Lower Threshold', color='green')
        
        # Add a legend
        axs[j][i].legend()

plt.tight_layout()
plt.show()

In [16]:
# change outliers to NaN
df1 = df[defaults.x_data]

mask = (z_scores.abs() > 2)
mask.head()

df1[mask] = pd.NA

df1.head()

C:\Users\20223037\AppData\Local\Temp\ipykernel_5892\676677244.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1[mask] = pd.NA
C:\Users\20223037\AppData\Local\Temp\ipykernel_5892\676677244.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1[mask] = pd.NA


EState_VSA7  SMR_VSA10  fr_thiazole  PEOE_VSA3     Chi1v    MolWt  \
0     0.000000  17.469783          0.0   0.000000       NaN      NaN   
1    12.990104  22.570184          0.0   4.794537  5.444609  250.681   
2     0.000000  11.814359          0.0   0.000000  4.955455  210.277   
3     0.000000  11.033401          0.0   0.000000  5.146222  232.239   
4     0.000000  11.600940          0.0   4.794537  4.708338  226.663   

       Chi1  PEOE_VSA14  BCUT2D_LOGPHI  NumAromaticRings  ...  PEOE_VSA1  \
0       NaN    0.000000       2.061950               1.0  ...  11.467335   
1  8.058551    5.625586       2.220550               2.0  ...   9.154014   
2  7.201907    0.000000            NaN               NaN  ...  10.633577   
3  8.163902    5.559267       2.062716               2.0  ...  10.044842   
4  7.112591    5.689743            NaN               1.0  ...   0.000000   

   HeavyAtomMolWt  SMR_VSA9  VSA_EState6    AvgIpc  FractionCSP3     Chi3v  \
0             NaN  0.000000     0.000000       NaN      0.166667       NaN   
1         239.593  5.749512     6.779888       NaN      0.153846  2.427385   
2         192.133  0.000000     0.000000       NaN      0.454545       NaN   
3         220.143  0.000000     6.777354  2.361815      0.166667  2.439419   
4         215.575  0.000000     0.000000       NaN      0.200000  2.091973   

    LabuteASA  BCUT2D_MRLOW  RingCount  
0         NaN           NaN        NaN  
1  103.266383      0.359025        2.0  
2   90.432235     -0.121740        NaN  
3   97.719850     -0.585723        2.0  
4   91.727399      0.625699        NaN  

[5 rows x 56 columns]

In [17]:
z_scores.head()

EState_VSA7  SMR_VSA10  fr_thiazole  PEOE_VSA3     Chi1v     MolWt  \
0    -1.175423  -0.430402    -0.217199  -1.099842 -2.814060 -2.735972   
1    -0.462403   0.040364    -0.217199  -0.132285 -1.603756 -1.351495   
2    -1.175423  -0.952396    -0.217199  -1.099842 -1.848186 -1.913645   
3    -1.175423  -1.024479    -0.217199  -1.099842 -1.752860 -1.608083   
4    -1.175423  -0.972095    -0.217199  -0.132285 -1.971670 -1.685663   

       Chi1  PEOE_VSA14  BCUT2D_LOGPHI  NumAromaticRings  ...  PEOE_VSA1  \
0 -2.678282   -0.596609      -1.975101         -1.310474  ...  -0.153464   
1 -1.488561    0.901640      -0.496781         -0.282723  ...  -0.497684   
2 -1.832140   -0.596609      -3.066639         -2.338224  ...  -0.277526   
3 -1.446307    0.883977      -1.967966         -0.282723  ...  -0.365130   
4 -1.867963    0.918726      -2.828947         -1.310474  ...  -1.859791   

   HeavyAtomMolWt  SMR_VSA9  VSA_EState6    AvgIpc  FractionCSP3     Chi3v  \
0       -2.732022 -0.816254    -1.893256 -3.287658     -0.934815 -2.508038   
1       -1.300796 -0.000897    -0.590407 -2.043558     -1.010806 -1.594691   
2       -1.997530 -0.816254    -1.893256 -2.104006      0.771521 -2.081069   
3       -1.586331 -0.816254    -0.590894 -1.702442     -0.934815 -1.586702   
4       -1.653391 -0.816254    -1.893256 -2.165192     -0.737239 -1.817383   

   LabuteASA  BCUT2D_MRLOW  RingCount  
0  -2.727697      2.883751  -2.024871  
1  -1.401121      1.195078  -1.060811  
2  -1.836655      0.010275  -2.988931  
3  -1.589345     -1.133172  -1.060811  
4  -1.792703      1.852273  -2.024871  

[5 rows x 56 columns]

In [18]:
fingerprint_data = df['SMILES'].apply(smiles_to_fingerprint)

finger_print = pd.DataFrame(fingerprint_data)

finger_print.head()
df2 = pd.DataFrame(finger_print['SMILES'].to_list(), columns=[f'Fingerprint_{i}' for i in range(len(finger_print['SMILES'][0]))])

merged_df = pd.concat([df2, df1, df], axis=1)
merged_df.head(50)

Fingerprint_0  Fingerprint_1  Fingerprint_2  Fingerprint_3  Fingerprint_4  \
0               0              0              0              0              0   
1               0              0              0              1              0   
2               0              0              0              0              0   
3               0              0              0              0              0   
4               0              0              0              0              0   
5               0              0              0              0              0   
6               0              0              0              0              0   
7               0              0              0              0              0   
8               0              1              0              0              0   
9               0              1              0              0              0   
10              0              1              0              0              0   
11              0              0              0              0              0   
12              0              1              0              0              0   
13              0              0              0              0              0   
14              0              0              0              0              0   
15              0              0              0              0              0   
16              0              0              0              0              0   
17              0              0              0              0              0   
18              0              0              0              0              0   
19              0              0              0              0              0   
20              0              0              0              0              0   
21              0              0              0              0              0   
22              0              0              0              0              0   
23              0              0              0              0              0   
24              0              0              0              0              0   
25              0              0              0              0              0   
26              0              0              0              0              0   
27              0              0              0              0              0   
28              0              0              0              0              0   
29              0              0              0              0              0   
30              0              0              0              0              0   
31              0              0              0              1              0   
32              0              0              0              0              1   
33              0              0              0              0              0   
34              0              0              0              0              0   
35              0              0              0              0              0   
36              0              0              0              0              0   
37              0              0              0              0              0   
38              0              0              0              0              0   
39              0              1              0              0              0   
40              0              0              0              0              0   
41              0              0              0              0              0   
42              0              0              0              0              0   
43              0              0              0              0              0   
44              0              0              0              0              0   
45              0              0              0              0              0   
46              0              0              0              0              0   
47              0              0              0              0              1   
48              0              0   

In [19]:
# Remove columns that have a Nah
dropped_df = merged_df.dropna()

In [20]:
merged_df.to_csv('./datasets/prepared_data.csv')